$$\newcommand\N{\mathbb N}$$
$$\newcommand\Z{\mathbb Z}$$
$$\newcommand\R{\mathbb R}$$
$$\renewcommand\phi{\varphi}$$
$$\newcommand\Zphi{\mathbb Z[\varphi]}$$
$$\renewcommand\bar{\overline}$$

# L'anneau $\Zphi$ (I)

Marc Lorenzi

8 décembre 2022

In [ ]:
import matplotlib.pyplot as plt
import math

## 1. Un sous-anneau de $\R$

### 1.1 Introduction

L'équation $x^2-x-1=0$ d'inconnue $x\in\R$ possède deux solutions réelles que nous noterons $\phi$ et $\bar\phi$. Nous choisissons pour $\phi$ la racine positive. Nous allons dans ce notebook étudier quelques propriétés de l'ensemble $\Zphi\subseteq\R$ défini par

$$\Zphi=\{a+b\phi: (a, b)\in\Z^2\}$$

Remarquons tout de suite la propriété essentielle suivante.

**Proposition.** Tout élément de $\Zphi$ s'écrit de façon unique $a+b\phi$ où $a,b\in\Z$.

**Démonstration.** Soit $x\in\Zphi$. L'existence de l'écriture résulte de la définition de $\Zphi$. Supposons que $x=a+b\phi=c+d\phi$ où $a,b,c,d\in\Z$. On a donc
$$a-c=(d-b)\phi$$

Supposons, par l'absurde, que $b\ne d$. On a alors

$$\phi=\frac{a-c}{d-b}\in\mathbb Q$$

contradiction. Ainsi, $b=d$. En reportant, il vient $a=c$.

**Vocabulaire.**  Pour tout $x=a+b\phi\in\Zphi$, où $a,b\in\Z$, nous appellerons $a$ et $b$ les *coordonnées* de $x$. Plus précisément, nous appellerons $a$ la *partie réelle* de $x$ et $b$ sa *partie imaginaire* (bien que les éléments de $\Zphi$ soient tous des réels).

Nous représenterons les éléments $\Zphi$ en Python par les objets de la classe `ZPhi`. Cette classe contient le code nécessaire pour manipuler le plus naturellement possible les éléments de $\Zphi$. Telle quelle elle ne sait pas faire grand chose : ses méthodes appellent des fonctions que nous écrirons tout au long du notebook.

In [ ]:
class ZPhi:
    
    def __init__(self, a, b=0):
        self.re = a
        self.im = b
        
    def coords(self):
        return (self.re, self.im)
        
    def str_im(self, b):
        p = '\u03C6'
        if b == -1: return '-' + p
        elif b == 1: return p
        else: return str(b) + p
    
    def __str__(self):
        p = '\u03C6'
        a, b = self.re, self.im
        if b == 0:
            return str(a)
        elif a== 0: return self.str_im(b)
        elif b < 0: return str(a) + self.str_im(b)
        else: return str(a) + '+' + self.str_im(b)
        
    def __repr__(self):
        return str(self)
        
    def __eq__(self, other):
        if isinstance(other, int): other = ZPhi(other)
        return self.re == other.re and self.im == other.im
        
    def __add__(self, other):
        if isinstance(other, int): other = ZPhi(other)
        return add_zphi(self, other)
    
    def __radd__(self, other): return self + other
    
    def __mul__(self, other):
        if isinstance(other, int): other = ZPhi(other)
        return mul_zphi(self, other)
    
    def __rmul__(self, other): return self * other
    def __neg__(self): return ZPhi(-self.re, -self.im)
    def __sub__(self, other): return self + (-other) 
    def __rsub__(self, other): return -(self - other)
    
    def conj(self): return conj_zphi(self)
    def N(self): return norme_zphi(self)
    def est_inversible(self): return est_inversible_zphi(self)
    def inverse(self): return inverse_zphi(self)
    def __truediv__(self, other): return self * other.inverse()
    def __rtruediv__(self, other): return ZPhi(other) / self
    
    def __pow__(self, n):
        if n < 0: return (self ** (-n)).inverse()
        else:
            z = ZPhi(1)
            m = n
            y = self
            while m != 0:
                if m % 2 == 1: z = z * y
                m = m // 2
                y = y * y
            return z
        
    def __divmod__(self, other):
        if isinstance(other, int): other = ZPhi(other)
        return divmod_zphi(self, other)

    def __rdivmod__(self, other): return divmod(ZPhi(other), self)

    def __floordiv__(self, other):
        q, r = self.__divmod__(other)
        return q

    def __rfloordiv__(self, other): return ZPhi(other) // self
    
    def __mod__(self, other):
        q, r = self.__divmod__(other)
        return r

    def __rmod__(self, other): return ZPhi(other) % self

La seule méthode de cette classe que nous ayons à utiliser est la méthode `coords`. Si $x$ est un objet de la classe `ZPhi`, l'appel `x.coords()` renvoie l'unique couple $(a,b)$ d'entiers relatifs tel que $x=a+b\phi$.

Nous aurons également à *construire* des objets de la classe `ZPhi`. Étant donnés $a,b\in\Z$, pour créer l'objet $a+b\phi$ il suffit d'appeler `ZPhi(a, b)`. le second paramètre est optionnel et vaut 0 par défaut.

Par exemple, la variable globale `phi` représente le réel $\phi$.

In [ ]:
phi = ZPhi(0, 1)

La classe `ZPhi` sait afficher joliment ce nombre.

In [ ]:
print(phi)

### 1.2 Structure d'anneau

**Proposition.** $\Z[\phi]$ est un sous-anneau de $\mathbb R$. 

**Démonstration.** 

- $1=1+0\phi\in\Zphi$.
- Soient $x,y\in\Zphi$. Soient $a,b,c,d\in\Z$ tels que $x=a+b\phi$ et $y=c+d\phi$. On a

$$x+y=(a+b\phi)+(c+d\phi)=(a+c)+(b+d)\phi\in\Zphi$$

- Soient $x,y\in\Zphi$. Soient $a,b,c,d\in\Z$ tels que $x=a+b\phi$ et $y=c+d\phi$. En remarquant que $\phi^2=\phi+1$ on a, en développant,

$$xy=(a+b\phi)\times(c+d\phi)=(ac+bd)+(ad+bc+bd)\phi\in\Zphi$$

Les opérations sont immédiates à écrire en Python. Voici les fonctions d'addition et de multiplication.

In [ ]:
def add_zphi(x, y):
    a, b = x.coords()
    c, d = y.coords()
    return ZPhi(a + c, b + d)

In [ ]:
def mul_zphi(x, y):
    a, b = x.coords()
    c, d = y.coords()
    return ZPhi(a * c + b * d, a * d + b * c + b * d)

Grâce à la classe `ZPhi`, nous pouvons opérer sur les élements de $\Zphi$ de façon naturelle. La soustraction est déjà définie par la classe : pour tous $x,y\in\Zphi$, $x-y=x+(-y)$.

De même, l'élévation à une puissance entière est déjà définie. La méthode qui effectue cette opération utilise pour les puissances positives l'algorithme d'*exponentiation rapide*. Comme pour l'instant nous n'avons pas carcatérisé l'inverse d'un élément de $\Zphi$, évitons les puissances négatives.

In [ ]:
(3 + 5 * phi) - (2 - 4 * phi)

In [ ]:
(3 + 8 * phi) * (2 - 4 * phi)

In [ ]:
(3 - phi) ** 1000

## 2. Morphismes

### 2.1 Conjugué

Pour tout $x\in\Zphi$ de coordonnées $a,b\in\Z$, le **conjugué** de $x$ est $\overline x = a + b\overline\phi$, où $\overline\phi$ est la deuxième racine de l'équation $x^2-x-1=0$. Les relations coefficients-racines nous donnent

$$\phi+\overline\phi=1\quad\text{et}\quad\phi\overline\phi=-1$$

On a donc

$$\overline x= a+b\overline\phi=a+b(1-\phi)=(a+b)-b\phi$$

In [ ]:
def conj_zphi(x):
    a, b = x.coords()
    return ZPhi(a + b, -b)

Nous pouvons dorénavant utiliser la méthode `conj` de la classe `ZPhi`.

In [ ]:
(5 - 2 * phi).conj()

**Proposition.** Pour tout $x\in\Zphi$, $\overline x=x$ si et seulement si $x\in\Z$.

**Démonstration.** Soit $x\in\Zphi$ de coordonnées $a,b\in\Z$.

$(\Rightarrow)$ Supposons $\overline x=x$. On a donc $a+b\phi=a+b\overline\phi$, d'où $b(\phi-\overline\phi)=0$. Comme $\phi\ne\overline\phi$, on a donc $b=0$, d'où $x=a\in\Z$.

$(\Leftarrow)$ Supposons $x\in\Z$. On a $x=x+0\phi$ et donc $\overline x =x+0\overline\phi=x$.

**Lemme.** $\overline{\overline\phi}=\phi$.

**Démonstration.** $\overline{\overline\phi}=\overline{1-\phi}=1-\overline\phi=\phi$.

Voici une démonstration pythonesque de ce résultat.

In [ ]:
phi.conj()

In [ ]:
phi.conj().conj()

**Proposition.** L'application $x\longmapsto\overline x$ est un automorphisme de l'anneau $\Zphi$ égal à sa réciproque. 

**Démonstration.**

- $\overline 1 =\overline{1+0\phi}=1+0\overline\phi=1$.
- Soient $x,y\in\Zphi$. Soient $a,b$ les coordonnées de $x$ et $c,d$ les coordonnées de $y$. On a

$$\overline{x+y}=\overline{(a+c)+(b+d)\phi}=(a+c)+(b+d)\overline\phi$$

et

$$\overline x +\overline y=(a+b\overline\phi)+(c+d)\overline\phi=(a+c)+(b+d)\overline\phi$$

Ainsi, $\overline{x+y}=\overline x+\overline y$.

- De même (avec un peu plus de calculs), on a pour tous $x,y\in\Zphi$, $\overline{xy}=\overline x\times \overline y$.

- Soit $x\in\Zphi$ de coordonnées $a,b\in\Z$. On a, grâce aux deux propriétés précédentes,

$$\overline{\overline x}=\overline{a+b\overline\phi}=\overline a+\overline b\ \overline{\overline\phi}$$

Comme $a,b\in\Z$, $\overline a=a$ et $\overline b=b$. De là, en utilisant le lemme,

$$\overline{\overline x}=a+b\phi=x$$

### 2.2 Norme

Pour tout $x\in\Zphi$, la **norme** de $x$ est $\mathcal N(x)=x\overline x$.

In [ ]:
def norme_zphi(x):
    return x * x.conj()

Nous pouvons dorénavant utiliser la méthode `N` de la classe `ZPhi`.

In [ ]:
phi.N()

In [ ]:
(3 + 4 * phi).N()

**Proposition.** Pour tous $x,y\in\Zphi$, $\mathcal N(xy)=\mathcal N(x)\mathcal N(y)$.

**Démonstration.** Soient $x,y\in\Zphi$. On a

$$\mathcal N(xy)=(xy)\overline{xy}=xy\overline x\ \overline y=(x\overline x)(y\overline y)=\mathcal N(x)\mathcal N(y)$$

**Proposition.** Pour tout $x\in\Zphi$, $N(x)\in\Z$.

**Démonstration.** Soit $x\in\Zphi$. On a

$$\overline{\mathcal N(x)}=\overline{x\overline x}=\overline x\ \overline{\overline x}=\overline xx=\mathcal N(x)$$

Ainsi, $\mathcal N(x)$, égal à son conjugué, appartient à $\Z$.

## 3. Les inversibles

### 3.1 Introduction

Notons $\mathcal U$ le groupe des inversibles de l'anneau $\Z[\phi]$.

**Proposition.** Soit $x\in\Zphi$. On a $x\in\mathcal U$ si et seulement si $\mathcal N(x)=\pm 1$.

**Démonstration.**

$(\Rightarrow)$ Supposons $x\in\mathcal U$. Soit $x'$ l'inverse de $x$. On a $xx'=1$ et donc

$$\mathcal N(x)\mathcal N(x')=\mathcal N(xx')=\mathcal N(1)=1$$

Ainsi, $\mathcal N(x)$ est inversible dans l'anneau $\Z$, donc $\mathcal N(x)=\pm 1$.

$(\Leftarrow)$ Supposons $\mathcal N(x)=\pm 1$. On a alors $x\overline x=\pm 1$. Ainsi, $x$ est inversible et $x^{-1}=\pm\overline x$.

Plus précisément,

- Si $\mathcal N(x)=1$ alors $x$ est inversible et son inverse est $\overline x$.
- Si $\mathcal N(x)=1$ alors $x$ est inversible et son inverse est $-\overline x$.

In [ ]:
def est_inversible_zphi(x): return x.N() in [-1, 1]

In [ ]:
def inverse_zphi(x):
    if x.N() == 1: return x.conj()
    elif x.N() == -1: return -x.conj()
    else: raise Exception('Non inversible')

Voici les inversibles de $\Zphi$ dont les coordonnées appartiennent à $[|-20,20|]$, ainsi que leur inverse. Nous pouvons dorénavant utiliser la méthode `est_inversible` de la classe `ZPhi`.

In [ ]:
N = 20
for a in range(-N, N + 1):
    for b in range(-N, N + 1):
        x = a + b * phi
        if x.est_inversible():
            print('%10s%10s' % (x, x.inverse()))

### 3.2 Représentation graphique

Soit $x\in\Zphi$ de coordonnées $a,b$. On a

$$\mathcal N(x)=x\overline x=(a+b\phi)(a+ b\overline\phi)=a^2+ab(\phi+\overline\phi)+b^2\phi\overline\phi=a^2+ab-b^2$$

Ainsi, $x$ est inversible si et seulement si $a^2+ab-b^2=\pm 1$. Soient $(\mathcal H)$ et $(\mathcal H')$ les courbes d'équations

$$(\mathcal H)\ x^2+xy-y^2=1$$

$$(\mathcal H')\ x^2+xy-y^2=-1$$

Ces deux courbes sont des hyperboles. Leur équation est plus simple si on effectue une rotation de repère. La fonction de rotation est donnée par

$$\begin{pmatrix}x\\y\end{pmatrix}=\frac 1{\sqrt{\phi^2+1}}\begin{pmatrix}1&-\phi\\ \phi&1\end{pmatrix}\begin{pmatrix}X\\Y\end{pmatrix}$$

On vérifie aisément que si $x,y\in\Z$, alors $x+\phi y\in\mathcal U$ si et seulement si $XY=\pm c$, où $c=\frac{\phi^2+1}{5\phi}$.

Je ne commenterai pas le code des fonctions ci-dessous.

In [ ]:
def rotation(X, Y):
    p = (1 + math.sqrt(5)) / 2
    x = (X - p * Y) / (math.sqrt(p ** 2 + 1))
    y = (p * X + Y) / (math.sqrt(p ** 2 + 1))
    return (x, y)

In [ ]:
def rotation_liste(Xs, Ys):
    n = len(Xs)
    xs, ys = [], []
    for k in range(500):
        X, Y = Xs[k], Ys[k]
        x, y = rotation(X, Y)
        xs.append(x)
        ys.append(y)    
    return (xs, ys)

In [ ]:
def subdi(a, b, n):
    d = (b - a) / n
    return [a + k * d for k in range(n +1)]

In [ ]:
def tracer_hyperboles(N):
    opt = {'color':'k', 'lw':1}
    p = (1 + math.sqrt(5)) / 2
    c = (p ** 2 + 1) / (5 * p)
    Xs = subdi(-2*N, -0.001, 500)
    Ys = [c / x for x in Xs]
    xs, ys = rotation_liste(Xs, Ys)
    plt.plot(xs, ys, **opt)
    Xs = subdi(0.001, 2*N, 500)
    Ys = [c / x for x in Xs]
    xs, ys = rotation_liste(Xs, Ys)
    plt.plot(xs, ys, **opt)
    Xs = subdi(-2*N, -0.001, 500)
    Ys = [-c / x for x in Xs]
    xs, ys = rotation_liste(Xs, Ys)
    plt.plot(xs, ys, **opt)
    Xs = subdi(0.001, 2*N, 500)
    Ys = [-c / x for x in Xs]
    xs, ys = rotation_liste(Xs, Ys)
    plt.plot(xs, ys, **opt)
    plt.xlim(-N, N)
    plt.ylim(-N, N)

In [ ]:
def plot_inversibles(N):
    p = (1 + math.sqrt(5)) / 2
    tracer_hyperboles(N)
    plt.plot([-N, N],[-N * p, N * p], 'r', lw=1)
    plt.plot([-N, N],[-N * (1 - p), N * (1 - p)], 'r', lw=1)
    xs = []
    ys = []
    for a in range(-N, N +1):
        for b in range(-N, N + 1):
            if (a + b * phi).est_inversible():
                xs.append(a)
                ys.append(b)
    plt.plot(xs, ys, 'ok', ms=3)
    plt.xticks(range(-N, N + 1))
    plt.yticks(range(-N, N + 1))
    plt.grid()
    plt.savefig('fig01.png', bbox_inches='tight')

In [ ]:
plt.rcParams['figure.figsize'] = (8, 8)

In [ ]:
plot_inversibles(10)

### 3.2 Une description du groupe $\mathcal U$

**Proposition.** $\mathcal U=\{\pm\phi^n:n\in\Z\}$.

**Démonstration.** Remarquons que $\mathcal N(-1)=1$, donc $-1\in\mathcal U$. De même, $\mathcal N(\phi)=\phi\overline\phi=-1$, donc $\phi\in\mathcal U$. De là, puisque $\mathcal U$ est un groupe, on a pour tout $n\in\Z$, $\pm\phi^n\in\mathcal U$.

La preuve de l'inclusion réciproque est un peu longue pour figurer ici. Nous l'admettrons.

Nous pouvons maintenant lister facilement les éléments de $\mathcal U$.

In [ ]:
for k in range(-20, 21):
    print(phi ** k, end=', ')
    print(-phi ** k, end=', ')

Voici un « gros » inversible de $\Zphi$. Remarquons que notre notion de « grosseur » est due à notre nature d'êtres euclidiens. En effet, le nombre affiché ci-dessous, en tant qu'habitant du monde $\Zphi$, est de norme 1 !

In [ ]:
print(phi ** 2022)

### 3.3 Inversibles et nombres de Fibonacci

Considérons la suite de Fibonacci $(F_n)_{n\in\mathbb N}$ définie par $F_0=0$, $F_1=1$ et pour tout $n\in\mathbb N$, $F_{n+2}=F_{n+1}+F_n$.

**Proposition.** Pour tout $n\in\mathbb N^*$, $\phi^n=F_{n-1}+F_n\phi$.

**Démonstration.** Montrons le résultat par une récurrence sur $n$. 

- $\phi^1=\phi=F_{0}+F_1\phi$.
- Soit $n\in\mathbb N$. Supposons que $\phi^n=F_{n-1}+F_n\phi$. On a alors

$$\begin{array}{lll}
\phi^{n+1}&=&\phi^n\phi\\
&=&(F_{n-1}+F_n\phi)\phi\\
&=&F_{n-1}\phi+F_n\phi^2\\
&=&F_{n-1}\phi+F_n(1+\phi)\\
&=&F_{n}+(F_{n-1}+F_n)\phi\\
&=&F_{n}+F_{n+1}\phi\\
\end{array}$$

Nous voici en possession d'une fonction d'une ligne permettant de calculer le $n$ième nombre de Fibonacci.

In [ ]:
def fibonacci(n): return (phi ** n).im

Juste pour voir, que se passe-t-il si nous appelons `fibonacci` avec un paramètre $n< 0$ ?

In [ ]:
for n in range(11):
    print(n, fibonacci(n), fibonacci(-n))

Ceci suggère de prolonger la suite de Fibonacci en suite $(F_n)_{n\in\Z}$ en posant pour tout $n<0$, $F_n=(-1)^{n-1}F_{-n}$. On laisse au lecteur le soin de prouver la proposition suivante :

**Proposition.** Pour tout $n\in\Z$, $\phi^n=F_{n-1}+F_n\phi$.

In [ ]:
for n in range(-10, 0):
    print('%10s%10s' % (phi ** n, fibonacci(n - 1) + phi * fibonacci(n)))

Ainsi, les coordonnées des éléments de $\mathcal U$ sont des nombres de Fibonacci ou des opposés de nombres de Fibonacci.

**Remarque.** La fonction `fibonacci` est terriblement efficace. Le calcul de $\phi^n$ est effectué, dans la classe `ZPhi`, au moyen de l'algorithme d'exponentiation rapide, qui nécessite $O(\log n)$ opérations. Ainsi, la fonction `fibonacci` calcule $F_n$ en seulement $O(\log n)$ opérations. Bien entendu, ce sont des opérations sur de grands entiers, et on ne peut pas considérer ces opérations comme des opérations « élémentaires ». 

Cela dit, `fibonacci` est réellement efficace. À titre d'exemple, voici le 20000$^e$ nombre de Fibonacci.

In [ ]:
fibonacci(20000)

Rien n'empêche de calculer le millionième nombre de Fibonacci. Le calcul est instantané.

In [ ]:
f = fibonacci(1000000)

N'essayez pas de l'afficher, vous obtiendrez un message d'erreur. Ceci est dû à Jupyter, qui limite la taille des objets affichés. Quelle est la taille de ce nombre ? On a pour tout $n\in\mathbb N$,

$$F_n=\frac{\phi^n-\overline\phi^n}{\sqrt 5}\sim \frac{\phi^n}{\sqrt 5}$$

De là, le nombre de chiffres de $F_n$ en base 10 est $1+\lfloor\log F_n\rfloor\sim n\log \phi$.

In [ ]:
print(1000000 * math.log((1 + math.sqrt(5)) / 2))

Environ 500000 chiffres ...

## 4. Et ensuite ?

Dans $\Zphi$ (comme dans tout anneau), on dispose de la relation de divisibilité. Si $x,y\in\Zphi$, $x$ divise $y$ s'il existe $z\in\Zphi$ tel que $y=xz$. Ceci ouvre la perspective de faire dans l'anneau $\Zphi$ de *l'arithmétique*.

Dans l'anneau plus « primitif » $\Z$ des entiers relatifs, on dispose d'une division euclidienne. Grâce à celle-ci on peut définir, via l'algorithme d'Euclide, le pgcd de deux entiers relatifs. On peut également s'intéresser aux nombres premiers, qui sont les entiers n'admettant que des factorisations triviales.

Nous allons voir dans le notebook suivant (disponible à la demande) qu'on peut faire de même dans $\Zphi$. Pour tous $x,y\in\Zphi$ tels que $y\ne 0$, il existe $q,r\in\Zphi$ tels que

$$\left\{\begin{array}{l}
x=qy+r\\
|\mathcal N(r)|< |\mathcal N(y)|
\end{array}\right.$$

L'anneau $\Zphi$ est plus « riche » que l'anneau $\Z$, et l'étude de son arithmétique promet des résultats intéressants. Histoire de nous motiver, tout le monde sait que 5 est un nombre premier. Oui, certes, dans l'anneau $\Z$. Mais qu'en est-il dans $\Zphi$ ? Eh bien 5 n'est alors plus premier. En effet,

$$5 = (2+\phi)(2+\overline\phi)$$

De plus, 

$$\mathcal N(2+\phi)=\mathcal N(2+\overline\phi)=5$$

Ces deux nombres sont donc non inversibles, ce sont des facteurs *non triviaux* de 5.

Dans le prochain notebook, entre autres choses, nous parlerons de division euclidienne et de pgcd, et nous caractériserons complètement les éléments premiers de $\Zphi$. Bien entendu, tout ceci sera accompagné de fonctions Python explicites et de jolis dessins.